# Тематическое моделирование

Задача тематического моделирования состоит в том, чтобы разложить слова, употребляющиеся в корпусе на темы и приписать эти темы каждому документу в корпусе.

Помимо анализа тематического наполнения корпуса, тематическое моделирование может использоваться для:

1) построения вектроных представлений текстов (числа показывают насколько тема выражена в тексте). Такие представления могут быть лучше обычных (TfidfVectorizer, CountVectorizer), т.к. позволяют находить близкие документы даже если в них нет одинаковых слов (но есть слова одной тематики). Тематические векторы могут использоваться для поиска, рекомендаций или как признаки в классификации. 

2) приписывания тэгов текстам. Так можно автоматически выделять в текстовых потоках тренды, горячие темы. Тэги можно использовать как фильтр в поисковых системах. Тэги нужно приписывать темам вручную, но это проще чем размечать обучающую выборку, так как слова в тематике сразу подказывают название. 

3) составления тематических словарей



Кроме обычных текстов тематическое моделирование применяется к многим другим данным: запросам пользователей, сайтам, на которые заходят пользователи, музыке, которую слушают пользователи, покупкам в одной корзине, банковским транзакциям и даже днк. 


Все подходы к тематическому моделированию так или иначе основнованы на:

1) модели мешка слов (т.е. порядок слов в документах не учитывается)  
2) независимости документов между собой  (т.е. употребление слова W в тексте D_1 никак не влияет на слова в документе D_2)  
3) дистрибутивной гипотезе (слова, употребляющиеся вместе, объединяются в темы)



В этой тетрадке для получения тематических моделей используются LDA из gensim и NMF из sklearn.

Про LDA (и в целом тематическое моделирование) можно почитать вот эту статью - https://sysblok.ru/knowhow/kak-ponjat-o-chem-tekst-ne-chitaja-ego/

In [185]:
import gensim
import json
import re
import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from pymorphy2 import MorphAnalyzer
import pyLDAvis.gensim
import string
from collections import Counter
import warnings
warnings.filterwarnings("ignore")
from IPython.display import Image
from IPython.core.display import HTML 
morph = MorphAnalyzer()

## Данные

Возьмем 10 тыс статьи с Википедии. 

Токенизируем самым простым способом и нормализуем Pymorphy.

In [145]:
stops = set(stopwords.words('russian'))

# чтобы быстрее нормализовать тексты, создадим словарь всех словоформ
# нормазуем каждую 1 раз и положим в словарь
# затем пройдем по текстам и сопоставим каждой словоформе её нормальную форму

def opt_normalize(texts, top=None):
    uniq = Counter()
    for text in texts:
        uniq.update(text)
    
    norm_uniq = {word:morph.parse(word)[0].normal_form for word, _ in uniq.most_common(top)}
    
    norm_texts = []
    for text in texts:
        
        norm_words = [norm_uniq.get(word) for word in text]
        norm_words = [word for word in norm_words if word and word not in stops]
        norm_texts.append(norm_words)
        
    return norm_texts

def tokenize(text):
    words = [word.strip(string.punctuation) for word in text.split()]
    words = [word for word in words if word]
    
    return words

In [150]:
texts = open('wiki_data.txt').read().splitlines()[:10000]

In [151]:
len(texts)

10000

In [152]:
texts = opt_normalize([tokenize(text.lower()) for text in texts], 30000)

In [153]:
texts[:3]

[['нижегородский',
  '—',
  'сельский',
  'посёлок',
  'район',
  'нижегородский',
  'область',
  'входить',
  'состав',
  'расположить',
  '12,5',
  'километр',
  'юг',
  'село',
  '1',
  'километр',
  'запасть',
  'город',
  'право',
  'берег',
  'река',
  'правый',
  'приток',
  'река',
  'сатис',
  'окружить',
  'смешанный',
  'леса',
  'соединить',
  'дорогой',
  'посёлок',
  '1,5',
  'километр',
  'дорога',
  'посёлок',
  'сатис',
  '3,5',
  'километр',
  'название',
  'являться',
  'сугубо',
  'официальный',
  'местный',
  'население',
  'использовать',
  'исключительно',
  'название',
  '—',
  'употребляться',
  'языковой',
  'оборот',
  'ранее',
  'использовать',
  'название',
  '—',
  '1920-ха',
  'год',
  'переселенец',
  'соседний',
  'село',
  'аламасовый',
  'расположить',
  'соответственно',
  '8',
  '14',
  'километр',
  'запасть',
  'посёлок',
  'жить',
  'рабочий',
  'совхоз',
  'центр',
  'посёлок',
  'сатис',
  'возле',
  'посёлок',
  'расположить',
  'активно',
  '

In [59]:
# для нграммов
# ph = gensim.models.Phrases(texts, scoring='npmi', threshold=0.4) # threshold можно подбирать
# p = gensim.models.phrases.Phraser(ph)
# ngrammed_texts = p[texts]

### Тематическое моделирование в gensim

Для моделей нужно сделать словарь.

In [154]:
dictinary = gensim.corpora.Dictionary(texts)

In [155]:
dictinary.filter_extremes(no_above=0.1, no_below=10)
dictinary.compactify()

In [156]:
print(dictinary)

Dictionary(8711 unique tokens: ['1,2', '1,5', '12', '12,5', '14']...)


Преобразуем наши тексты в мешки слов. 

In [157]:
corpus = [dictinary.doc2bow(text) for text in texts]

Про параметры можно почитать в документации:

In [122]:
?gensim.models.LdaMulticore

Основные это num_topics, alpha, eta и passes. 

**num_topics** - это количество тем. Это основной параметр и настраивать его проще всего. Обычно 200 оптимальное значение. Можно поставить поменьше, если тексты не очень разнообразные или хочется уменьшить время обучения.

**alpha** и **eta** - параметры, которые влияют на разреженность распределения документы-темы и темы-слова. У alpha есть значения "asymmetric" и "auto", которые можно попробовать (по умолчанию стоит "symmetric", т.е. не разреженное). Eta можно задать каким-то числом или самому сделать изначальное распределение слов по темам. НО настраивать эти параметры сложно и непонятно и вообще лучше надеяться, что по умолчанию все заработает.

**passes** - задает количество проходов по данным. Чем больше, тем лучше сойдется модель, но обучаться будет дольше.

In [174]:
lda = gensim.models.LdaMulticore(corpus, 100, id2word=dictinary, eval_every=0, passes=10) # если поддерживается многопоточность
# lda = gensim.models.LdaModel(200, id2word=dictinary, passes=5)

Посмотрим на топики.

In [175]:
lda.print_topics()

[(5,
  '0.015*"сын" + 0.015*"брак" + 0.015*"де" + 0.009*"дочь" + 0.009*"французский" + 0.008*"отец" + 0.008*"смерть" + 0.007*"ii" + 0.007*"вместе" + 0.007*"мария"'),
 (44,
  '0.033*"народичский" + 0.024*"ложа" + 0.015*"4140" + 0.014*"великое" + 0.013*"больница" + 0.013*"тверская" + 0.011*"области.############код" + 0.010*"великий" + 0.009*"знак" + 0.009*"медицинский"'),
 (20,
  '0.028*"игрок" + 0.010*"игровой" + 0.010*"уровень" + 0.009*"the" + 0.008*"каждый" + 0.008*"соревнование" + 0.006*"playstation" + 0.006*"компания" + 0.006*"выпустить" + 0.006*"комплекс"'),
 (65,
  '0.069*"улица" + 0.027*"станция" + 0.027*"дом" + 0.016*"линия" + 0.013*"москва" + 0.009*"построить" + 0.008*"век" + 0.008*"сторона" + 0.008*"проходить" + 0.007*"строительство"'),
 (97,
  '0.027*"герб" + 0.016*"тысяча" + 0.016*"щит" + 0.011*"луи" + 0.008*"осетия" + 0.007*"южный" + 0.006*"пол" + 0.005*"данные" + 0.005*"золотой" + 0.005*"текст"'),
 (19,
  '0.025*"windows" + 0.022*"турнир" + 0.020*"снукер" + 0.018*"ружински

Ещё есть штука для визуализации.

In [176]:
pyLDAvis.enable_notebook()

In [177]:
pyLDAvis.gensim.prepare(lda, corpus, dictinary)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
98     0.075556  0.145861       1        1  5.547647
83    -0.102599  0.133229       2        1  4.798338
88    -0.032908 -0.164809       3        1  4.162770
25     0.044178 -0.123835       4        1  3.707913
73     0.013129 -0.004514       5        1  3.131183
18    -0.225484 -0.061467       6        1  2.775693
29     0.028365  0.087725       7        1  2.731440
43     0.087495  0.033453       8        1  2.723281
95    -0.024069 -0.181125       9        1  2.583982
89    -0.243212 -0.009244      10        1  2.472966
6      0.137715 -0.140843      11        1  2.060938
5     -0.014138  0.070620      12        1  2.050905
2      0.087482 -0.193944      13        1  1.883013
42     0.155749 -0.060352      14        1  1.799852
64     0.007283 -0.000044      15        1  1.793457
71     0.054910 -0.001377      16        1  1.753201
75     0.052906 -0.067390      17        1  1.747179
58    -0.010399  0.011862      18        1  1.735172
11     0.054434 -0.021077      19        1  1.680524
21    -0.009586 -0.011203      20        1  1.650836
84     0.056495  0.165766      21        1  1.593456
47    -0.263241 -0.083740      22        1  1.568696
92    -0.053205  0.122122      23        1  1.553337
0      0.040310  0.073973      24        1  1.550593
78     0.163729 -0.176344      25        1  1.512196
76    -0.082056  0.095951      26        1  1.480235
48     0.026907 -0.013890      27        1  1.458688
7      0.105370  0.026276      28        1  1.458229
15     0.084068  0.046215      29        1  1.423583
85    -0.109581  0.007884      30        1  1.331902
41    -0.158629 -0.079011      31        1  1.229131
37     0.027022  0.024420      32        1  1.067505
45    -0.004496  0.029790      33        1  1.019368
65     0.099503 -0.068244      34        1  0.999334
28     0.062234 -0.058663      35        1  0.988938
36    -0.056546  0.067344      36        1  0.919018
82    -0.024629 -0.080279      37        1  0.896359
8      0.054750 -0.013641      38        1  0.818632
60    -0.223285 -0.100555      39        1  0.816675
12     0.019642  0.108634      40        1  0.810387
9     -0.045641  0.095339      41        1  0.782620
50     0.019741  0.022653      42        1  0.769428
62    -0.052331  0.072725      43        1  0.693772
49    -0.031483  0.018900      44        1  0.662686
86    -0.104618  0.034310      45        1  0.649634
77     0.032410 -0.009718      46        1  0.647645
70    -0.072299 -0.037229      47        1  0.628340
81     0.006483  0.102972      48        1  0.610022
91     0.097281 -0.140101      49        1  0.609914
56    -0.067790  0.018566      50        1  0.576955
90     0.065116 -0.142201      51        1  0.563611
30     0.053984  0.026003      52        1  0.550341
24     0.046470  0.040014      53        1  0.543865
10     0.032696  0.042191      54        1  0.542521
52    -0.026376 -0.004562      55        1  0.534831
46    -0.172422 -0.145316      56        1  0.509572
59     0.013372  0.125534      57        1  0.467095
19    -0.149829 -0.013875      58        1  0.460167
20    -0.057086  0.067798      59        1  0.449159
40    -0.047816  0.114301      60        1  0.435548
80     0.020271  0.042106      61        1  0.413234
38    -0.039650 -0.111935      62        1  0.404827
31    -0.020155  0.039696      63        1  0.400643
13     0.016240  0.099582      64        1  0.369484
68     0.016897  0.070553      65        1  0.369228
57    -0.033820  0.021810      66        1  0.369027
26     0.021898  0.067967      67        1  0.366231
1      0.006962  0.068080      68        1  0.363066
97     0.052961  0.019928      69        1  0.361107
34     0.053864  0.056885      70        1  0.338428
96     0.008720  0.073674      71        1  0.336459
44     0.044300  0.011727      72        1  0.334378
33    -0.013594  0.052994      73        1  0.3

На графике должно быть как можно меньше пересекающихся кружков (т.е. темы состоят из разных слов), а сами кружки не должны быть огромными (скорее всего такую тему можно разбить на несколько поменьше).

Можно посмотреть метрики.

In [178]:
import numpy as np

Перплексия показывает насколько хороше моделируется корпус. Чем ближе к нулю, тем лучше. Можно использовать, чтобы настраивать количество проходов по корпусу (когда перестало улучшаться, то можно останавливаться).

In [179]:
lda.log_perplexity(corpus[:1000])

-15.314779464084427

Ещё есть когерентность. Она численно оценивает качество тем (проверяется, что темы состоят из разных слов и что в теме есть топ тематических слов). 

In [180]:
coherence_model_lda = gensim.models.CoherenceModel(model=lda, 
                                                  texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

Чем выше, тем лучше.

In [181]:
topics = []
for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

In [182]:
coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [183]:
coherence_model_lda.get_coherence()

0.5158220538704145

Но все эти числа вспомогательны! Главные критерии качества модели: интерпретируемость и понятность тем (т.е. нужно глазами смотреть на каждую тему), а также польза для практической задачи, которую вы пытаетесь решить.

### Разложение матриц в sklearn

In [187]:
Image(url="https://www.researchgate.net/profile/Andrea_Bertozzi/publication/312157184/figure/fig1/AS:448453387001860@1483931027472/Conceptual-illustration-of-non-negative-matrix-factorization-NMF-decomposition-of-a.png",
     width=800, height=500)


NMF - превращает одну матрицу Words * Documents в произведение двух матриц Words * Topics и Topics * Documents (произведение не точно равно изначальной матрице, но достаточно близко - чем больше Topics, тем точнее, но больше тратиться памяти и времени). 

Таким образом, взяв одну из получившихся матриц, мы получим или тематические представления документов (вторая матрица - документы на темы), либо слова, разложенные по темам (первая матрица - темы на слова).

Отличие от LDA в том, что числа в матрицах не будут вероятностями, а просто каким-то положительными числам. Чем больше, тем сильнее слово или документ связан с темой. 

(Почему и как это все работает, вы можете почитать отдельно. Для практических задач хватит умения запускать все в sklearn) 

In [188]:
from sklearn.decomposition import NMF
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
import pandas as pd

Sklearn принимает на вход строки, поэтому склеим наши списки.

In [189]:
stexts = [' '.join(text) for text in texts]

Сделаем матрицу слова-документы с помощью TfidfVectorizer

In [198]:
vectorizer = TfidfVectorizer(max_features=2000, min_df=10, max_df=0.1, ngram_range=(1,2))
X = vectorizer.fit_transform(stexts)

Разложим её.

In [200]:
# n_components - главный параметр в NMF, это количество тем. 
# Если данных много, то увеличения этого параметра сильно увеличивает время обучения
model = NMF(n_components=100)

In [201]:
model.fit(X)

NMF(alpha=0.0, beta_loss='frobenius', init=None, l1_ratio=0.0, max_iter=200,
  n_components=100, random_state=None, shuffle=False, solver='cd',
  tol=0.0001, verbose=0)

In [202]:
model.components_.shape # матрица темы на слова

(100, 2000)

In [203]:
model.transform(X).shape # матрица документы на темы

(10000, 100)

In [204]:
pd.set_option('display.max_columns', 100)
pd.set_option('display.max_rows', 100)

Вытащим словарь, по которому мы построили модель.

In [205]:
feat_names = vectorizer.get_feature_names()

Теперь посмотрим на матрицу темы-слова, отсортируем её по строкам и возьмем топ N слов, сопоставив индексы со словарём

In [206]:
top_words = model.components_.argsort()[:,:-5:-1]

for i in range(top_words.shape[0]):
    words = [feat_names[j] for j in top_words[i]]
    print(i, "  ".join(words))

0 летний олимпийский  летний  олимпийский игра  участие летний
1 украина основать  год находиться  области код  составлять человек
2 отец  сын  дом  ребёнок
3 расстояние километр  харьковский  расстояние  километр
4 зимний олимпийский  зимний  олимпийский игра  участие зимний
5 украина находиться  области код  составлять человек  ул
6 новоград  новоград волынский  волынский  области население
7 матч  забить  гол  футболист
8 хутор  ростовский  район ростовский  ростовский области
9 ул  наш ул  карл  области население
10 растение  личинка  питаться  лист
11 книга  писатель  роман  журнал
12 овручский  области код  великий  сергей
13 остров  относиться  километр  побережье
14 емильчинский  области код  украина находиться  великий
15 населить пункт  населить  пункт  государство
16 уезд  год уезд  специальный район  округ
17 хорошевский  области население  украина находиться  украина основать
18 альбом  выпустить  выйти  записать
19 коростенский  области код  украина основать  год находить

У разложения есть метрика, показывающая насколько хорошо восстанавливается изначальная матрица. Чем меньше, тем лучше.

In [207]:
model.reconstruction_err_

75.4863850671827

Но как и с LDA - главное это польза от модели и человеческая оценка, получаемых тем.

## Домашнее задание

Основаная задача - **построить хорошую тематическую модель с интерпретируемыми топиками с помощью LDA в gensim и NMF в sklearn**.


1) сделайте нормализацию (если pymorphy2 работает долго используйте mystem или попробуйте установить быструю версию - `pip install pymorphy2[fast]`, можно использовать какой-то другой токенизатор); 

2) добавьте нграммы (в тетрадке есть закомменченая ячейка с Phrases,  можно также попробовать другие способы построить нграммы); 

3) сделайте хороший словарь (отфильтруйте слишком частотные и редкие слова, попробуйте удалить стоп-слова); 

4) постройте несколько LDA моделей (переберите количество тем, можете поменять alpha, passes), если получаются плохие темы, поработайте дополнительно над предобработкой и словарем; 

5) для самой хорошей модели в отдельной ячейке напечатайте 3 хороших (на ваш вкус) темы;

6) между словарем и обучением модели добавьте tfidf (`gensim.models.TfidfModel(corpus, id2word=dictionary); corpus = tfidf[corpus]`);

7) повторите пункт 4 на преобразованном корпусе;

8) в отдельной ячейке опишите как изменилась модель (приведите несколько тем, которые стали лучше или хуже, или которых раньше вообще не было; можно привести значения перплексии и когерентности для обеих моделей)

9) проделайте такие же действия для NMF (образец в конце тетрадки), для построения словаря воспользуйтесь возможностями Count или Tfidf Vectorizer (попробуйте другие значение max_features, min_df, max_df, сделайте нграмы через ngram_range, если хватает памяти), попробуйте такие же количества тем

10) в отдельной ячейки напечатайте темы лучшей NMF модели, сравните их с теми, что получились в LDA.

Сохраните тетрадку с экспериментами и положите её на гитхаб, ссылку на неё укажите в форме.

**Оцениваться будут главным образом пункты 5, 8 и 10. (2, 3, 2 баллов соответственно). Чтобы заработать остальные 3 балла, нужно хотя бы немного изменить мой код на промежуточных этапах (добавить что-то, указать другие параметры и т.д). **